---
# Jupyter Tutorial:
# Multi-Variate Analyse - maschinelles Lernen

Beispiel mit scikit-learn 
---
                                               
                                                      G. Quast, Jan. 2025            

Die Klassifizierung von Datensätzen, die unterschiedlichen Klassen entstammen
und jeweils mehrere Variablen enthalten, sind typische Aufgaben in der Physik.
Beispiele sind die Unterscheidung von Signal- bzw. Untergrund (oder "Rauschen")
in Messdaten, die Identifikation von Teilchenspuren in der Kern-, Teilchen- oder
Astroteilchenphysik oder die Erkennung neuer Effekte zusätzlich zu Standardprozessen.

Diese seit langem in der Physik etablierten Methoden wurden "Multivariate Analyse" (MVA) 
genannt und sind ein Beispiel für Techniken des sogenannten "Maschinellen Lernens".
Große Mengen an Daten in modernen Experimenten einerseits und die stark angewachsene 
Rechenleistung von Computern andererseits führen dazu, dass entsprechende Techniken
in der modernen Datenauswertung unverzichtbar geworden sind. 

Üblicherweise bestehen die Daten aus einer Reihe von Merkmalen (engl. "features"),
die abhängig von der jeweiligen Klasse unterschiedliche Verteilungen aufweisen. 
Dabei werden sehr häufig parameterfreie Modellierungen der Signal- und Untergrundverteilungen verwendet, die entweder aus simulierten oder unter 
speziellen Bedingungen aufgenommenen realen Daten abgeleitet und deren Unterscheidung
vom Algorithmus "gelernt" wird. 

Methoden des Maschinellen Lernens sind immer dann notwendig wenn klassische,
z.B. auf der analytischen Darstellung von Likelihoods beruhende Verfahren zur
Datenauswertung nicht ausreichen, weil die Likelihood-Funktion im Detail
gar nicht bekannt, nicht analytisch dargestellt und bei Vorliegen vieler
Variablen auch nicht zuverlässig parametrisiert werden kann. 


Dieses Jupyter-Notebook veranschaulicht die übliche Vorgehensweise unter Verwendung 
des sehr mächtigen Pakets *scikit-learn*. Das hier behandelte einfache Beispiel verwendet 
den auf einer einfachen Likelihood beruhenden Klassifikator 
`sklearn.naive_bayes.GaussianNB`, um die einzelnen Schritte zu veranschaulichen.  
*GaussianNB* entspricht einer klassischen Likelihood-Analyse,
bei der davon ausgegangen wird, dass die einzelnen Merkmale *x_i* des Merkmalsvektors
**X** gaußverteilt und unabhängig voneinander sind. Die einzelnen Zeilen des 
Merkmalsvektors gehören zu einer von zwei Klassen, „0“ und „1“, mit Mittelwerten
$\mu_0$ und $\mu_1$ und Varianzen ${\sigma_0}^2$ und ${\sigma_1}^2$. 
Diese beiden Parameter pro Klasse werden aus Stichproben mit bekannten Klassenzuordnungen
bestimmt. Beim maschinellen Lernen wird dieser Schritt „Training“ genannt, in *scikit-learn*
bezeichnet man ihn als "fit". Der so vorbereitete Klassifikator wird dann auf neue Daten 
angewandt, um die Klassenzugehörigkeit vorherzusagen.

Der *GaussNB*-Klassifikator ist bzgl. des Rechenaufwands sehr effizient.
Die Annahme von Normalverteilungen vereinfacht die Berechnung der Wahrscheinlichkeiten, 
da nur der Mittelwert und die Standardabweichung geschätzt werden müssen, anstatt 
die vollständige Wahrscheinlichkeitsverteilung der einzelnen Merkmale zu bestimmen. 
Dieser Klassifikator kann auch für Daten verwendet werden, die den Annahmen nicht genügen, 
aber in solchen Fällen gibt es in der Regel bessere Methoden zur Klassifizierung.

Die allgemeinen Schritte eines Klassifizierungsproblems  sind

  1. Aufbereitung der Daten in einem geeigneten Format (hier ein Zufallsdatensatz)
  2. Aufteilung der Daten in Trainings- und Validierungs- (=Test-) Stichproben,
     Normierung auf Mittelwert Null und Varianz Eins der Merkmale     
  3. Daten visualisieren 
  4. Auswahl eines Klassifikators und Trainieren (= Anpassen)
  5. Testen der Leistungsfähigkeit anhand der Validierungsstichprobe
      - Klassifikator-Ausgabe
      - Entscheidungsgrenzen
      - Verwechslungsmatrix
      - mehrere „Scores“ zur Beurteilung der Qualität (z. B. Effizienz, Reinheit)
      - Untersuchung der Abhängigkeit von der Klassifizierungsschwelle

Die Implementierung in diesem Beispiel ist sehr allgemein, und daher ist es leicht,
den Klassifikator *GaussNB* durch andere in *scikit-learn* verügbare oder auch selbst 
programmiere Klassifikatoren zu ersetzen, die eine ganze Reihe anderer, meist nicht 
auf einer parametrisierten Darstellung einer Likelihood beruhende Methoden nutzen. 

Die folgende Code-Zelle enthält die Importe aller notwendigen Pakete:

In [ ]:
# Code based on example from https://scikit-learn.org/
#   extended version for RNP by Günter Quast

"""Illustrate multivariate analysis with scikit-learn

This example uses the classifier `sklearn.naive_bayes.GaussianNB`
to illustrate the general steps performed in a typical classification
task. The chosen classifier assumes that individual features *x_i* the
features Vector **X** are Gaussian distributed and independent of one
another. They belong to one of two classes, "0" and "1", with
means X_i_0 and X_i_1 and variances V_i_0 and V_i_1. The classifier is
fit to a data sample with known class assignments. In machine
learning, this step called "training". The trained classifier
is then applied predict the class of new data.

The *GaussNB* classifier is computationally very efficient.
The assumption of normal distributions simplifies the calculation
of probabilities, because only the mean and standard deviation
need bo estimated instead of the full probability distribution
of each feature. This classifier can also be used on data with
features not satisfying the assumptions, however, in such cases,
better classification methods usually exist.

The general steps of a classification task are

  1.  Prepare data in suitable format (here a random data set)
  2.  split data in training and validation (=test) samples
  3.  inspect data
  4.  choose a classifier and train (=fit) it
  5.  test performance on validation sample
      - classifier output
      - decision boundaries
      - confusion matrix
      - several "scores", i.e. efficiency, purity
      - study dependence on classifier threshold (ROC curve)

The implementation in this example is rather general, and therefore
it is easy to replace *GaussNB* by other *scikit-learn* classifiers.
"""

# imports
# - general
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap

#  - generate (random) data
from sklearn.datasets import make_classification

#  - classifier(s)
from sklearn.naive_bayes import GaussianNB
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import FixedThresholdClassifier

#  - helpers to
#    - prepare training and test samples
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

#    - show quality of classification
from sklearn.inspection import DecisionBoundaryDisplay
from sklearn.metrics import ConfusionMatrixDisplay
from sklearn.metrics import classification_report, confusion_matrix, roc_curve, auc

### 1. Erzeugen und Vorbereiten der Daten

Datensätze für *scikit-learn* werden als zweidimensionale *numpy*-Arrays, *X*,
bereit gestellt, deren Zeilen einzelnen Stichproben entsprechen. 
Die Spalten entsprechen den Werten der einzelnen Merkmale. 
Ein zweiter eindimensionaler *numpy*-Array, *y*, enthält die Klassenzuordnungen 
der einzelnen Stichproben; die Klassen werden durch einen Klassenindex repräsentiert, 
in unserem einfachen Beispiel durch die Werte "0" und "1".

*scikit-learn* enthält eine Methode zur Erzeugung zufälliger Daten, 
`make_classification`, mit deren Hilfe Cluster von gaußverteilten Daten
erzeugt werden können, um Studien zu verschiedenen Klassifikationsalgorithmen
durchzuführen. 

In [ ]:
# 1. --- prepare resp. generate data set

# - three features, two classes with two Gaussian clusters per class
n_features = 3  # number of features
feature_names = ["feature" + str(i) for i in range(n_features)]
Nclusters_per_class = 2  # Gaussian blobs per class
Rseed = 31415  # fixed random seed
n_classes = 2
class_names = ['0', '2']
#   (GaussNB classifier is not the best for this type of problem ...)
X, y = make_classification(
    n_samples=5000,
    n_features=n_features,
    n_informative=n_features,
    n_redundant=0,
    n_classes=n_classes,
    n_clusters_per_class=Nclusters_per_class,
    weights=[0.5, 0.5],
    random_state=Rseed,
)
print("Merkmal-Vektor X")
display(X)
print("Klassenzugehörigkeit y")
display(y)

### 2. Trainings- und Validierungsdaten, Skalierung der Daten

Die klassifizierten Daten werden im zweiten Schritt zufällig in zwei Datensätze
aufgeteilt. Der erste wird zur Bestimmung der Parameter des Klassifikators, also zum
Training verwendet. Der zweite Datensatz dient zur Überprüfung der Leistungsfähigkeit
auf einer unabhängigen Stichprobe. Viele Klassifikatoren benötigen standardisierte 
Eingabedaten in einem vorgegebenen Wertebereich. Dazu gibt es eine *Python*-Klasse 
*StandardScaler', die die Werte der Merkmale auf eine Verteilung mit Mittelwert 
Null und Varianz Eins skaliert. Die dazu notwendige Transformation wird auf den 
Trainingsdaten bestimmt  und auch auf alle weiteren Datensätze angewendet.  

In [ ]:
# 2. --- split data in training and test samples and normalize

# . generate data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.4, random_state=2)

# - scale to mean 0 and variance 1
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)  # transformation from training data
X_test = scaler.transform(X_test)  # apply transformation to test data
X = scaler.transform(X)  # apply transformation to all data

### 3. Visualisierung der Daten

Um mögliche Auffälligkeiten wie "Ausreißer" oder Fehler bei der Datenbereitstellung
zu identifizieren und eine optimale Methode zur Klassifikation auszuwählen, besteht
der erste Schritt einer jeden Datenauswertung darin, die Daten sorgfältig anzuschauen.
Dazu gehören zunächst klassische Verfahren wie die Bestimmung der Korrelationen der 
Merkmale, insbesondere aber auch deren Visualisierung in Form von Verteilungen und
Streudiagrammen. 

In [ ]:
# 3. --- inspect the data

#  means, standard deviations and correlations
print("\nmean, std. dev. and correlations of input data:")
keys = [f"feature{i}" for i in range(n_features)]
for _ic in range(n_classes):
    _X = X[y == _ic]
    print("Class", class_names[_ic])
    print("  key           mean    std     correlations")
    means = np.asarray([_X[:, i].mean() for i in range(n_features)])
    stds = np.asarray([_X[:, i].std() for i in range(n_features)])
    cormat = np.corrcoef(_X, rowvar=False)
    for i in range(len(keys)):
        print(f"{keys[i]:10s}: {means[i]:10.4g} {stds[i]:6.04g}   ", end='')
        for j in range(i):
            print(f"{cormat[i,j]:5.2f} ", end='')
        print()

#   histograms and scatter plots of features
fig_features = plt.figure(figsize=(4.5 * n_features, 4.5 * n_features))
fig_features.suptitle("Overview of feature space", size='xx-large')
plt.tight_layout()
cm = plt.cm.RdBu
cm_bright = ListedColormap(["#FF0000", "#0000FF"])
for i in range(n_features):
    _pidx = (n_features + 1) * i + 1
    for j in range(i, n_features):
        _ax = fig_features.add_subplot(n_features, n_features, _pidx)
        if j == n_features - 1:
            _ax.set_xlabel(feature_names[i])
        if i == 0 and j != 0:
            _ax.set_ylabel(feature_names[j])
        _pidx += n_features
        if j == i:  # show histograms of features
            _ax.hist((X[y == 1, i], X[y == 0, i]), 75, color=('blue', 'red'))
            continue
        #   show scatter plots of features
        #   - for training points
        _ax.scatter(X_train[:, i], X_train[:, j], marker='o', c=y_train, cmap=cm_bright, s=7, alpha=0.75)
        #   - for testing points
        _ax.scatter(X_test[:, i], X_test[:, j], marker='+', c=y_test, cmap=cm_bright, s=7, alpha=0.75)

### 4. Auswahl und Training des Klassifikators

Die Korrelationskoeffizienten der Daten sind in diesem Beispiel zwar klein, aber 
die grafische Darstellung zeigt dennoch deutliche Korrelationen der Teildatensätze, 
aus denen die Stichproben der einzelnen Klassen zusammengesetzt sind. Ein einfacher, 
auf der  Annahme gaußverteilter Daten beruhender Klassifikator ist daher nicht die 
optimale Wahl, zeigt aber dennoch recht gute Trenneigenschaften und wird daher an dieser 
Stelle ausgewählt.   
*Anmerkung:* Mit dem Wert "1" für den zur Datenerzeugung verwendeten Parameter
*n_clusters_per_class* wäre diese Wahl allerdings optimal.

Wir wählen hier den Klassifikator *GaussianNB*, der auf einer auf Gaußverteilungen 
basierenden Likelihood-Analyse basiert. Der Zusatz "NB = Naive Bayes" bedeutet dabei, 
dass die Merkmale als unkorreliert angenommen werden. Die Likelihood-Funktionen der Merkmale 
$x_i$ für die Klassen $y=0, 1$ hängen nur von den Erwartungswerten $\mu_{0, 1}$ und den 
Standardabweichungen $\sigma_{0,1}$ ab, die aus den Trainingsdaten bestimmt werden:

$$P(x_i \mid y) = \frac{1}{\sqrt{2\pi\sigma^2_y}} 
  \exp\left(-\frac{(x_i - \mu_y)^2}{2\sigma^2_y}\right)$$

Wie für die Klassifikatoren in *scikit-learn* üblich, liefert auch dieser Klassifikator 
einen kontinuierlichen Ausgabewert $y_{prd} \in [0, 1]$, der die Wahrscheinlichkeit 
der Klassenzugehörigkeit repräsentiert. 

Übrigens können viele andere Klassifikatoren in *scikit-learn* mit dem ansonsten 
gleichen Code direkt verwendet werden. Eine auskommentierte Zeile zeigt, wie man 
alternativ ein künstliches neuronales Netz (MPLClassifier, MLP = Multi-Layer Perceptron) 
verwenden kann. 

Nach der Initialisierung wird der Klassifikator mit den oben erzeugten Trainingsdaten 
trainiert - in der Nomenklatur von *scikit-learn* heißt dieser Schritt "*fit*". 

In [ ]:
# 4. --- select a classifier and train it

# - default classifier for this example
classifier = GaussianNB()  # Gauss likelihood assuming independent features ("Naive Bayes")

### optional modifications: select more powerful classifiers

#  select own implementation of a Classifier based on the Multivariate Gauss Likelihood
# from GaussLClassifier import GaussLClassifier # from this directory
# classifier = GaussLClassifier()

#  - Quadratic Discriminant Analysis (like GaussianNB(), but with feature covariances)
# classifier = QuadraticDiscriminantAnalysis()

# - Artificial Neural Network classifier
# classifier = MLPClassifier(hidden_layer_sizes=(10,), max_iter=1000, random_state=42)

###  end optional part

# - use new feature in scikit-learn 1.6: set decision threshold for classifier
clf_threshold = 0.5
clf = FixedThresholdClassifier(classifier, threshold=clf_threshold, response_method="predict_proba")
# - "train" classifier
clf_trained = clf.fit(X_train, y_train)

### 5. Analyse der Ergebnisse 

#### 5.1 Darstellung des Klassifikator-Outputs

Nach Ausführen der *fit()*-Methode können mit Hilfe der Methoden *predict(x)* bzw.
*predict_proba(x)* Vorhersagen zur Klassenzugehörigkeit bzw. der Wahrscheinlichkeit
der Kasssenzugehörigkeit eines Merkmalvektors *X* gewonnen werden: 
`y_prd = clf.predict_proba(X)`.

*Anmerkung:* die Ausgabe enthält zwei Vektoren, die Wahrscheinlichkeiten der Zuordnung
zu Klasse '0' bzw. '1'. Wir verwenden unten den zweiten davon, dessen Ausgabe für die 
erste Klasse in der Nähe von Null und für die zweite Klasse bei Eins liegt.

Um einen Eindruck der Qualität der Klassifikation zu bekommen, ist es zunächst hilfreich,
die Ausgabe des Klassifikators für die einzelnen Klassen darzustellen. Außerdem
kann in den oben erzeugten Streudiagrammen die Klassifikator-Ausgabe als Farbcode
angezeigt werden. Die ist in der Code-Zelle unten gezeigt. 

In [ ]:
# 5. -- analyze results

#   - evaluate classifier on training data
#       use prediction of class 1, i.e. distributed around 0 for class 0 and around one for 1
y_prd1 = clf.predict_proba(X_train)[:, 1]

#    - show classifier output for classes
fig_clf = plt.figure(figsize=(5.0, 5.0))
fig_clf.suptitle("classifier output", size='xx-large')
ax_clf = fig_clf.add_subplot()
_ = ax_clf.hist(y_prd1[y_train == 1], bins=100, color='blue', ec='grey', alpha=0.8, label="class 1")
_ = ax_clf.hist(y_prd1[y_train == 0], bins=100, color='red', ec='grey', alpha=0.3, label="class 0")
ax_clf.set_ylabel("frequency")
ax_clf.set_xlabel("Predictor output")
ax_clf.set_yscale('log')
plt.legend()

# - show classifier output in feature space (for pairs of indices)
fig_decisionboundaries = plt.figure(figsize=(4.5 * (n_features - 1), 4.5 * (n_features - 1)))
fig_decisionboundaries.suptitle("Decision Boundaries in feature space", size='xx-large')
plt.tight_layout()
for i in range(n_features - 1):
    _pidx = n_features * i + 1
    for j in range(i + 1, n_features):
        _ax = fig_decisionboundaries.add_subplot(n_features - 1, n_features - 1, _pidx)
        if j == n_features - 1:
            _ax.set_xlabel(feature_names[i])
        if i == 0:
            _ax.set_ylabel(feature_names[j])
        #   show scatter plots of features
        #   - for training points
        _ax.scatter(X_train[:, i], X_train[:, j], marker='o', c=y_train, cmap=cm_bright, s=7, alpha=0.3)
        #   - for testing points
        _ax.scatter(X_test[:, i], X_test[:, j], marker='+', c=y_test, cmap=cm_bright, s=7, alpha=0.3)
        #   show decision boundaries - have to train for each feature
        _X_train = np.column_stack((X_train[:, i], X_train[:, j]))
        _X = np.column_stack((X[:, i], X[:, j]))
        _clf = FixedThresholdClassifier(classifier, threshold=clf_threshold, response_method="predict_proba")
        _clf_trained = _clf.fit(_X_train, y_train)
        DecisionBoundaryDisplay.from_estimator(_clf, _X, cmap=cm, alpha=0.3, ax=_ax)
        _pidx += n_features - 1

#### 5.2 Kennzahlen der Klassifikation auf Validierungsdatensatz

Zur Beurteilung der Qualität der Klassifikation wird der im Training nicht verwendete 
Test-Datensatz genutzt, der oben mit der Methode *train_test_split()* zufällig aus dem
gesamten Datensatz ausgewählt und abgetrennt wurde. 
Neben korrekt klassifizierten Ereignissen (true-positive, `tp`, und  true-negative, `tn`) 
treten sog. Fehler 1. und 2. Art, also dass Untergrund fälschlich als Signal akzeptiert 
(false-positive, `fp`) oder ein echtes Signal fälschlich verworfen wird 
("false-negative", `fn`). 

Für den Anteil solcher Fehlklassifizierungen gibt es im Jargon des Machine Learnings
zwei wichtige Größen, die Genauigkeit (*precision*) und die Sensitivität oder Effizienz 
(*recall*). 

Die **Genauigkeit** beschreibt, welcher Anteil von positiv klassifizierten Ereignissen 
tatsächlich zur Klasse gehört. Man kann das auch als Reinheit (oder purity) der 
klassifizierten Ereignisse bezeichnen : 

`precision = tp/(tp+fp)`.
   
Die **Sensitivität** beschreibt, welcher Anteil der tatsächlich zur Klasse
gehörenden Ereignisse korrekt zugewiesen wird: 

`recall = tp/(tp+fn)`. 

In der Praxis sind oft beide Größen wichtig. Daher definiert man einen weitere
Größe, **f1-score**, die den harmonischen Mittelwert (Kehrwert des Mittelwerts 
von Kehrwerten) von *precision* und *recall* darstellt. 

Die Anzahlen der `tp`-, `tn`-, `fp`- und `fn`-Klassifizierungen ergeben sich
aus den Vektoren der wahren und der vorhergesagten Klassenzuordnungen 
(`y` bzw. `y_pred`). Man ordnet sie auch gerne in einer Matrix an, der 
sog. Verwechslungsmatrix (confusion matrix):

    --------------------------------------------
    |         | pred. positiv  | pred. negativ |
    --------------------------------------------
    | positiv |      tp         |     fn       |
    | negativ |      fp         |     tn       |
    --------------------------------------------

In der Code-Zelle unten werden die diese Kenngrößen mit Hilfe von Methoden 
aus dem Paket *scikit-learn* berechnet und dargestellt. 

In [ ]:
#  - evaluation on test data
y_pred1 = clf.predict_proba(X_test)[:, 1]

#  - print scores
cm = confusion_matrix(y_test, y_pred1 > clf_threshold)
print("\nConfusion Matrix:")
print(cm)

print(15 * ' ' + "tp/(tp+fp)  tp/(tp+fn)")
print(15 * ' ' + "purity      efficiency    av        #")
print(classification_report(y_test, y_pred1 > clf_threshold, target_names=('class 0', 'class_1')))

# - nice display of confusion matrix
fig_cm = plt.figure(figsize=(5.0, 5.0))
ax_cm = fig_cm.add_subplot()
fig_cm.suptitle("Confusion Matrix", size='xx-large')
_ = ConfusionMatrixDisplay.from_estimator(clf, X_test, y_test, ax=ax_cm)

#### 5.3  Effizienz und Reinheit

Eine besonders für Anwendungen in der Physik wichtige Form der Darstellung ist ein Diagramm, 
das die Fehlerraten zeigt. Dazu wird die Schwelle zur Klassenzuordnung variiert und 
für jeden Wert der tru-positive und false-negative Anteil dargestellt. Ideal
ist ein möglichst hoher true-positve Anteil (Effizienz) beim niedrigstmöglichen Wert der 
false-positive Rate (Verunreinigung) bzw. der Reinheit (1. - false-positive Anteil). 
Die genaue Wahl des Optimums hängt vom konkreten Anwendungsfall ab, je nach dem, 
ob eine möglichst gute Untergrundunterdrückung oder ein möglichst signifikantes Verhältnis 
von Signal zu Untergrund erforderlich ist. 

Die Code-Zelle unten zeigt, wie man solche ROC-Kurven (ROC = "Receiver Operating Characteristic") 
erzeugt. Als Mass für die Qualität des Klassifikators dient häufig die Fläche unter der Kurve
(AUC = "Area Under Curve"). 

In [ ]:
# - ROC curve and AUC
fpr, tpr, thresholds = roc_curve(y_test, y_pred1)
roc_auc = auc(fpr, tpr)
# purity = tpr / (tpr + fpr)
# efficiency = tpr/(tpr + fnr)
fig_roc = plt.figure(figsize=(5.0, 5.0))
fig_roc.suptitle("ROC curve", size='xx-large')
ax_roc = fig_roc.add_subplot(1, 1, 1)
ax_roc.plot((0.0, 1.0), (0.0, 1.0), '--')
ax_roc.set_ylabel("true positive rate")
ax_roc.set_xlabel("false positive rate")
ax_roc.plot(fpr, tpr, '-', marker='.')
_t = ax_roc.text(0.25, 0.5, f"AUC={roc_auc:.3f}", transform=ax_roc.transAxes)

#### 5.4 Klassifikator Speichern und Wiederverwenden

Nachdem wir den Klassifikator konfiguriert, trainiert und charakterisiert haben, soll er möglicherweise 
für spätere Anwendungen archiviert werden. Dazu müssen die *Python*-Objekte zunächst mit Hilfe des
Pakets *pickle* in ein serielles Format gebracht und dann abgespeichert werden. 

Dies geht mit dem folgenden Code-Fragment: 

```
# - Save to disk using pickle #

import pickle

# save
with open('MVA-classifier.pkl', 'wb') as f:
    pickle.dump((scaler, clf, cm), f)
```

Das Einlesen und instantiieren der Objekte in einer anderen Anwendung ist ebenfalls sehr einfach:

```
import pickle

# load StandardScaler, Classifier and ConfusionMatrix
with open('MVA-classifier.pkl', 'rb') as f:    
    scaler, clf, cm  = pickle.load(f)
print("ML model loaded:\n", clf, '\n')
print("Confusion Matrix \n", cm, '\n')
```

Damit stehen die Datentransformation und der Klassifikator zur Verfügung,
und Daten im einem kompatiblen Merkmalvektor **X** können genau wie oben 
gezeigt klassifiziert werden:

```
y_pred = clf.predict_proba(X)
```


### Ändern des Klassifikators

In diesem Tutorial haben wir die grundsätzliche Vorgehensweise zur Klassifizierung 
von Daten kennen gelernt und dabei eine klassische, auf einer einfachen Gauß-Likelihood 
basierende Methode angewendet. 

Eine bessere Klassifizierung als oben gezeigt lässt sich erreichen, wenn man die 
Korrelationen der Merkmale ausnutzt, also die Likelihood der Klassenzugehörigkeit
auf Basis von multivariaten Gaußverteilungen bestimmt, die die Verteilungsdichte
der Merkmalvektoren näherungsweise beschreibt.  Ändern Sie dazu die in Abschnitt 4 
ausgewählte Methode und führen Sie die Code-Zellen Beispiels erneut aus. 
```
#  - Quadratic Discriminant Analysis (like GaussianNB(), but with feature covariances)
classifier = QuadraticDiscriminantAnalysis()
```
Diese Klassifikator zeigt eine sehr gute Performanz, obwohl die Merkmal-Verteilungen 
nicht perfekt beschrieben werden.

In der Praxis ist es vor allem bei sehr vielen Merkmalen kaum möglich, exakte
und auch noch analytisch darstellbare Verteilungsdichten im Merkmalraum anzugeben.
Dann werden Methoden benötigt, die diese Verteilungsdichten parameterfrei aus 
Beispieldaten lernen und auch noch gut über Stellen ohne gute Abdeckung interpolieren. 
Dazu eigenen sich zum Beispiel "Künstliche Neuronale Netze", die den funktionalen
Zusammenhang zwischen Merkmalvektoren als Eingabe und einer Klassenzuordnung abbilden
können. Ein solches künstliches neuronales Netzwerk besteht aus Knoten ("Perceptrons" oder "Neuronen"
genannt), die in Lagen angeordnet sind und durch gewichtete Verbindungen die Merkmale an den 
Eingängen zu einem Wert am Ausgang kombinieren. Die Gewichte werden dabei im Trainingsprozess
mit Hilfe von bereits korrekt klassifizierten Trainingsdaten optimiert. 
Einen auf einem künstlichen neuronalen Netzwerk basierenden Klassifikator können Sie auswählen,
wenn Sie im Code-Beispiel in Abschnitt 4 die ausgewählte Methode anpassen:
```
# - Artificial Neural Network classifier
classifier = MLPClassifier(hidden_layer_sizes=(10,), max_iter=1000, random_state=42)
```
Die einzelnen Schritte der Klassifikation verlaufen identisch wie vorher. Sie werden feststellen, 
dass der *MPLClassifier*  für den hier verwendeten Datensatz deutlich leistungsfähiger ist. 
Dafür ist der Aufwand im *fit*-Schritt aber auch höher, wie Sie an der längeren Laufzeit sehen.
Die Anwendung eines trainierten Netzes auf neue Daten zur Erzeugung einer Vorhersage ist aber 
auch numerisch sehr effizient. Die zur Klassifizierung relevanten Informationen werden in
den Gewichten kodiert, die die Neuronen verbinden. Wichtig ist auch die Topologie des gewählten
Netzes, insbesondere die Anzahl der Neuronen in der oder den mittleren (versteckten oder hidden)
Lagen des Netzes, d.h. der Parameter "*hidden_layer_sizes*" beim Ausführen der Initialisierung
von *MLPClassifier*. Es gibt noch viele weitere solcher "Hyperparameter", insbesondere um den
oft sehr aufwändigen Trainingsprozess zu steuern und zur sinnvollen Konvergenz zu bringen.   


### Vergleich verschiedener Klassifikatoren

Zum Abschluss wollen wir einige typische Klassifikatoren etwas detaillierter anschauen.
Dazu werden drei typische Datensätze verwendet:

1. zwei "linear trennbare" Klassen, die durch eine Hyperebene optimal unterschieden werden können,
2. zwei Klassen, die sich im Merkmalsraum wie Mondsicheln überlagern,
3. zwei Klassen, die kreisförmig, eine innerhalb der andern, angeordnet sind.
    *Übrigens*: Durch Parametertransformation in Polarkoordinaten könnte diese Konfiguration in
     eine linear trennbare überführt werden

Wir wollen einige verschiedene Arten von Klassifikatoren ausprobieren:

1. "Nearest Neighbors",
   Klassenzuordnung auf Grund der Mehrheit den *k* nächsten Nachbarn im Merkmalsraum;   
2. "Linear Support Vector Machine",
   Iterative Konstruktion einer optimalen Hyperebene zur Trennung von zwei Klassen im Merkmalsraum;  
3. "QDA , Quadratic Discriminant Analysis",
   Beschreibung der Verteilungsdichten der Punkte der einzelnen Klassen als multivariate
   Gaussverteilungen, Zuordnung eines Merkmalvektors *x* zur Klasse mit der größten Likelihood; 
4. "Gaussian Naive Bayes",
   wie 3., außer dass die Merkmale als unkorreliert angenommen werden. d.h. dass die
   Kovarianzmatrix diagonal ist;  
6. "Decision Tree",
   Entscheidungsbaum mit Knoten, die für eine Entscheidung auf Grundlage eines Merkmals stehen
   und den Datensatz iterativ in Teilmengen aufteilt, bis ein Abbruchkriterium erreicht ist;   
8. "Random Forest",
   ein großes Ensemble von Entscheidungsbäumen mit Klassenzuordnung auf Grund der Mehrheit der
   Einzelergebnisse;  
9. "Neural Network (MLP= Muli Layer Perceptron )" ,
   ein künstliches neuronales Netzwerk basierend auf einzelnen "Perceptrons" oder "Neuronen",
   die in Lagen angeordnet sind und durch gewichtete Verbindungen die Merkmale an den Eingängen
   zu einem Wert am Ausgang kombinieren.
    
Die Leistungsfähigkeit überprüfen wir mit Hilfe der Kennzahl "accuracy", die
den Anteil an korrekten Klassifizierungen angibt, `socre = (tp+tn)/(tp+fp+tn+fn)`.


In [ ]:
# Code source: Gaël Varoquaux
#              Andreas Müller
# Modified for documentation by Jaques Grobler
# simplified version for RNP by Günter Quast
# License: BSD 3 clause

# imports
#  - for data generation
from sklearn.datasets import make_blobs, make_circles, make_moons

# additional classifiers
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

# helper functions
from sklearn.pipeline import make_pipeline

classifiers = [
    KNeighborsClassifier(3),
    SVC(kernel="linear", C=0.025, random_state=42),
    QuadraticDiscriminantAnalysis(),
    GaussianNB(),
    DecisionTreeClassifier(max_depth=5, random_state=42),
    RandomForestClassifier(max_depth=5, n_estimators=10, max_features=1, random_state=42),
    MLPClassifier(hidden_layer_sizes=(100,), max_iter=1000, random_state=42),
]

cnames = [
    "Nearest Neighbors",
    "Linear SVM",
    "QDA",
    "Naive Bayes",
    "Decision Tree",
    "Random Forest",
    "Neural Net",
]

Nsamples = 300
datasets = [
    make_blobs(n_samples=Nsamples, n_features=2, centers=((-0.7, -0.7), (0.7, 0.7)), random_state=10),
    make_moons(n_samples=Nsamples, noise=0.3, random_state=11),
    make_circles(n_samples=Nsamples, noise=0.2, factor=0.5, random_state=12),
]

dnames = ['"linear"', '"moon"', '"circle"']

Nclassifiers = len(classifiers)
Ndatasets = len(datasets)

fig_classifiers = plt.figure(figsize=(2.5 * (Nclassifiers + 1), 2.5 * Ndatasets))
i = 1
# iterate over datasets
for ds_cnt, ds in enumerate(datasets):
    # preprocess dataset, split into training and test part
    X, y = ds
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)

    x_min, x_max = X[:, 0].min() - 0.5, X[:, 0].max() + 0.5
    y_min, y_max = X[:, 1].min() - 0.5, X[:, 1].max() + 0.5

    # just plot the dataset first
    cm = plt.cm.RdBu
    cm_bright = ListedColormap(["#FF0000", "#0000FF"])
    _ax = fig_classifiers.add_subplot(len(datasets), len(classifiers) + 1, i)
    if ds_cnt == 0:
        _ax.set_title("Input data")
    # Plot the training points
    _ax.scatter(X_train[:, 0], X_train[:, 1], marker='x', c=y_train, cmap=cm_bright)
    # Plot the testing points
    _ax.scatter(X_test[:, 0], X_test[:, 1], marker='+', c=y_test, cmap=cm_bright)
    _ax.set_xlim(x_min, x_max)
    _ax.set_ylim(y_min, y_max)
    _ax.set_xticks(())
    _ax.set_yticks(())
    _ax.text(0.075, 0.925, dnames[ds_cnt], color='darkblue', transform=_ax.transAxes)
    i += 1

    # iterate over classifiers
    for name, clf in zip(cnames, classifiers):
        _ax = fig_classifiers.add_subplot(len(datasets), len(classifiers) + 1, i)

        clf = make_pipeline(StandardScaler(), clf)
        clf.fit(X_train, y_train)
        score = clf.score(X_test, y_test)
        DecisionBoundaryDisplay.from_estimator(clf, X, cmap=cm, alpha=0.8, ax=_ax, eps=0.5)

        # Plot the training points
        # ax.scatter(
        #    X_train[:, 0], X_train[:, 1], makrer='x', c=y_train, cmap=cm_bright)
        # Plot the testing points
        _ax.scatter(X_test[:, 0], X_test[:, 1], marker='+', c=y_test, cmap=cm_bright)
        _ax.set_xlim(x_min, x_max)
        _ax.set_ylim(y_min, y_max)
        _ax.set_xticks(())
        _ax.set_yticks(())
        if ds_cnt == 0:
            _ax.set_title(name)
        _ax.text(
            x_max - 0.3,
            y_min + 0.3,
            ("%.2f" % score),
            size=15,
            horizontalalignment="right",
        )
        i += 1

plt.tight_layout()
plt.show()

### Eigenen Klassifikator erstellen

Es kann notwendig sein für Testzwecke oder zur optimalen Anpassung an eigene Problemstellungen
einen angepassten Klassifikator zur Verwendung mit *scikit-learn* selbst zu erstellen. Das
Application Programming Interface ("API") ist gut dokumentiert, siehe Link
[https://scikit-learn.org/1.5/developers/develop.html](https://scikit-learn.org/1.5/developers/develop.html).

Ein einfaches, aber nützliches Beispiel betrachten wir eine Eigenimplementierung, die 
multivariate Gaussverteilungen der Merkmale in jeder Klasse annimmt. Im Vergleich zu
*GaussNB* stellt dies auf dem hier betrachteten Testdatensatz eine deutliche Verbesserung
dar und entspricht dem *scikit-learn* Klassifikator *QuadraticDiscriminantAnalysis*.

In *scikit-learn* gibt es Basisklassen, mit deren Hilfe einige grundsätzliche Funktionen 
schon bereit gestellt werden. Implementiert werden müssen dann nur noch die Methoden
*fit()* und *predict()* oder *predict_proba()*. 

Im Beispiel unten werden in der *fit()*-Methode dazu die empirischen Mittelwerte und
die Kovarianzmatrix der Merkmale aus den Daten für jede Klasse bestimmt und dann mit 
diesen Werten die multivariaten Gaußverteilungen initialisiert.
Die Methode *predict(X)* gibt dann für jeden Merkmalvektor *X* die Klasse mit der 
maximalen Likelihood zurück. 
Zur Berechnung der Wahrscheinlichkeit der Klassenzugehörigkeit wird in der Methode
*predict_proba(X)* das Bayes'sche Theorem angewandt, um die Likelihood durch Normierung
in eine Wahrscheinlichkeit umzurechnen, d. h. der Likelihood-Wert für jede Klasse wird
auf die Summe der Likelihoods aller Klassen normiert.  

Die auf Basis der *scikit-learn* Vorlage mit nur wenigen Zeilen eigenem Code 
erstellte Implementierung sieht so aus: 

```python
import numpy as np
# --- for custom classifier
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.utils.validation import check_X_y, check_array, check_is_fitted
from sklearn.utils.multiclass import unique_labels

# multivariate Gauss distribution
from scipy.stats import multivariate_normal
from scipy.stats import norm

class GaussLClassifier(ClassifierMixin, BaseEstimator):
     """Implementation of a Gaussian Classifier based on multivariate Gaussian Likelihood

       Methods:

         predict(X):  predict class label with maximum likelihood from feature vector X
            Args: 
              X: feature vector of shape (n_rows, n_features)
            Retruns: 
              y: vector of shape (n_rows,) with class asignment    
       
         predict_proba(X):  predict class class probaility from feature vector X,
              calculated as Bayesian posterior probability from a uniform prior and the 
              likelihood of each feature vector X[i, :] for i in range(n_rows).

            Args: 
              X: feature vector of shape (n_rows, n_features)
            Returns: 
              y: array of shape (n_rows, n_classes) with probabilities that feature
                 vector in row i belongs to class j for each class j in range(n_classes)
    """
    
    def __init__(self, par=None):
        self.par = par

    def fit(self, X, y):
        # Check that X and y have correct shape
        X, y = check_X_y(X, y)
        # Store the classes (i.e. integer class labels) seen during fit
        self.classes_ = unique_labels(y)
        self.X_ = X
        self.y_ = y
        self.n_rows, self.n_features = np.shape(self.X_)

    # --- own code 
        # get means and covariance matrices of features per class
        self.means = (max(self.classes_) + 1) * [None]
        self.covmats = (max(self.classes_) + 1) * [None]
        self.pdfs = (max(self.classes_) + 1) * [None]
        for _ic in self.classes_:
            self.covmats[_ic] = np.cov(self.X_[y == _ic], rowvar=False)
            self.means[_ic] = self.X_[y == _ic].mean(axis=0)
        # set-up of multivariate Gauss distribution
            self.pdfs[_ic] = multivariate_normal(mean=self.means[_ic], cov=self.covmats[_ic])
            
        # check
        # print("classifier fit:\n means\n", self.means)
        # print(" covmats\n ", self.covmats)
    # ---    

        # Return the classifier
        return self

    def predict(self, X):
        # predict class based on maximum likelihood

        # Check if fit has been called
        check_is_fitted(self)
        # Input validation
        X = check_array(X)

    # --- own code 
        # calculate -2 log L of input
        Ls = np.array((max(self.classes_) + 1) * [0.0])
        for _ic in self.classes_:
            Ls[_ic] = self.pdfs[_ic].pdf(X)
        return np.argmax(Ls)

    def predict_proba(self, X):
        # predict approx. probability for each class using Bayes' theorem:
        #   prb(class) = likelihood(X, class) / sum_c likelihood(x, c)

        # Check if fit has been called
        check_is_fitted(self)
        # Input validation
        X = check_array(X)

    # --- own code 
        # calculate Likelihoods
        Ls = (1 + max(self.classes_)) * [None]
        Lsum = 0.
        for _ic in self.classes_:
            Ls[_ic] = self.pdfs[_ic].pdf(X)
            Lsum = Lsum + Ls[_ic]

        # calculate Bayesian posterior probabilities
        prbs = np.zeros((len(X), (1 + max(self.classes_))))
        for _ic in self.classes_:
            prbs[:, _ic] = Ls[_ic] / Lsum
        return np.asarray(prbs)
```

Diesen Klassifikator können Sie im Code oben verwenden, indem Sie
ihn aus dem lokalen Verzeichnis importieren und auswählen:
```python
from GaussLClassifier import GaussLClassifier # from this directory
#  select own implementation of  Multivariate Gauss likelihood
classifier = GaussLClassifier()
```


### Ausblick

Das Feld des maschinellen Lernens zeigt zu Zeit einige stürmische Entwicklungen, die auch
für die Physik von herausragender Bedeutung sind und vielfältige Anwendungsmöglichkeiten
haben. Momentan sind es sogenannte tiefe neuronale Netze ("Deep Learning"), die die Auswertung
großer Datensätze z.B. in der Teilchenphysik revolutioniert haben. 

Die Wahl des passenden Algorithmus sowie dessen effizientes und zuverlässiges Training und 
das Abwägen der Kosten in Form von Rechenzeit (oder Energieaufwand) im Vergleich zu erreichbaren 
Verbesserungen werden Sie in Zukunft oft beschäftigen. Dazu sind Detailkenntnisse zur Funktionsweise 
der verwendeten Algorithmen notwendig, die allerdings über den Rahmen dieser Einführung hinaus gehen
und Thema von Vertiefungskursen im Master-Studium sind.  